# Komputerowe wspomaganie tłumaczenia

# Zajęcia 11 - urównoleglanie

Na poprzednich zajęciach poznaliśmy techniki pozyskiwania tekstu z Internetu. Jeśli uda nam się w ten sposób pozyskać tekst w jednym języku oraz jego tłumaczenie na inny język, jesteśmy tylko o krok od uzyskania najbardziej przydatnego zasobu z punktu widzenia wspomagania tłumaczenia - pamięci tłumaczeń. Krokiem tym jest automatyczne urównoleglanie tekstu.

Automatyczne urównoleglanie tekstu składa się z dwóch kroków:
1. Podziału tekstu źródłowego oraz docelowego na zdania.
2. Dopasowaniu zdań źródłowych do docelowych.

Zdania, o których mowa w punkcie 1., powinniśmy rozumieć jako segmenty, tj. niekoniecznie kompletne zdania w sensie gramatycznym. Standardowym sposobem podziału tekstu na segmenty jest dzielenie po znaku nowej linii lub zaraz po kropce, o ile jest ona częścią sekwencji: ".[spacja][Wielka litera]"

### Ćwiczenie 1: Zaimplementuj podstawowy algorytm segmentacji tekstu. Użyj odpowiedniego wyrażenia regularnego, łapiącego wielkie litery w dowolnym języku, np. "Ż" (użyj klasy unikodowej). Zwróć listę segmentów.

In [116]:
import regex

def sentence_split(text):
    pattern = r'\s(?=\p{Lu})'
    segments = regex.split(pattern, text)
    return segments

text = "To jest przykładowy tekst. Nie wiem czym jest Python, ASCII i UNICODE. Ósmy raz sięgam ręką po borówkę. Żądło pszczoły jest kujące"
sentence_split(text)

['To jest przykładowy tekst.',
 'Nie wiem czym jest',
 'Python,',
 'ASCII i',
 'UNICODE.',
 'Ósmy raz sięgam ręką po borówkę.',
 'Żądło pszczoły jest kujące']

### Ćwiczenie 2: Uruchom powyższy algorytm na treści wybranej przez siebie strony internetowej (do ściągnięcia treści strony wykorzystaj kod z laboratoriów nr 7). Zidentyfikuj co najmniej dwa wyjątki od ogólnej reguły podziału na segmenty i ulepsz algorytm.

In [69]:
import regex as r
def sentence_split_enhanced(text):
    #Ulepszenie algorytmu: szukam indexu znaku białego który jest poprzedzany znakiem .?! i następuje po nim duża litera, ale przed znakiem musi wystąpić litera a-z (nie może) A-Z
    # Dltaego dodatkowmo nie dziele zdań gdy wystąpią skróty pokroju S.A. oraz w przypadku wystąpienia Dużej litery w środku zdania -> segment nie jest tworzony.
    # W dodatku obsługuję nawiasy () i [] -> pobieram zdania występujące w nawiasie

    pattern = r'(?<![A-Z])[.!?]\s+(?=\p{Lu})|\s*[\(\[](.*?)[\)\]]\s+'
    pattern = r'(?<![A-Z])[.!?]\s+(?=\p{Lu})|(?<=\()|(?=\))|(?<=\[)|(?=\])'
    segments = r.split(pattern, text)
    return segments
    
sentence_split_enhanced("Jeżeli chodzi o UNICODE czy ASCII to nie wiem co to jest. Jestem S444820 [Krystian Osiński] Lubię jeść pizze. Mam konto w banku Peako S.A i jestem z niego zadowolony.")


['Jeżeli chodzi o UNICODE czy ASCII to nie wiem co to jest',
 'Jestem S444820 [',
 'Krystian Osiński',
 '] Lubię jeść pizze',
 'Mam konto w banku Peako S.A i jestem z niego zadowolony.']

In [76]:
import re
import requests
from bs4 import BeautifulSoup

def get_text(url):

    page = requests.get(url)
    soup = BeautifulSoup(page.content, 'html.parser')

    # usunięcie elementów script i style
    for script in soup(["script", "style"]):
        script.extract()    # usuń element

    # pobierz tekst
    text = soup.get_text()

    # usuń wielokrotne białe znaki
    text = re.sub(r"\s+", " ", text)

    return(text)

In [77]:
sentence_split_enhanced(get_text("https://www.biznes.gov.pl/pl/portal/00169")) #podsatwowe info o spółce akcyjnej z portalu rządowego

[' Spółka akcyjna – podstawowe informacje | Biznes.gov.pl - Serwis informacyjno-usługowy dla przedsiebiorcy Przejdź do treści Przejdź do wyszukiwarki Przejdź do Centrum Pomocy gov.pl Serwis informacyjno-usługowy dla przedsiębiorcy × Zalogowany jako: e-Doręczenia Change language to English Ustawienia Wyloguj Logowanie Change language to English EN Biznes.gov.pl Informacje Katalog usług Wyszukiwarka firm Konto Przedsiębiorcy zamknij Konto Przedsiębiorcy Spółka akcyjna – podstawowe informacje Obserwuj Przeczytaj podstawowe informacje o spółce akcyjnej',
 'Sprawdź jakie są jej najważniejsze cechy, jak powstaje, jaki ma majątek, kto reprezentuje spółkę oraz na czym polega odpowiedzialność wspólników',
 'Kluczowe cechy spółki akcyjnej Umowa założycielska spółki akcyjnej Statut spółki spółki akcyjnej Firma - oznaczenie spółki akcyjnej Rejestracja spółki akcyjnej w KRS Rejestracja w ZUS i zgłoszenie do ubezpieczeń Strona internetowa spółki Akcje i prawa z nich wynikające Kapitał zakładowy spół

Po podziale tekstu na segmenty po stronie źródłowej oraz docelowej, możemy przystąpić do kroku drugiego - dopasowania segmentów. Głównym wyzwaniem tego kroku jest fakt, iż po stronie źródłowej może być inna liczba segmentów, niż po stronie docelowej. Takie rozbieżności są bardzo częste, a wynikają między innymi z:
* tłumaczenia jednego zdania źródłowego przy użyciu więcej niż jednego zdania
* tłumaczenia więcej niż jednego zdania źródłowego przy użyciu jednego zdania
* pominięcia zdania podczas tłumaczenia
* rozbieżności pomiędzy wersjami tekstu źródłowego i docelowego (np. tekst źródłowy mógł być modyfikowany po przetłumaczeniu i tłumaczenie nie zostało zaktualizowane)
* przetłumaczenia tekstu źródłowego tylko częściowo

Problemy te rozwiązwyane są na różne sposoby. Najpopularniejszym programem do przeprowadzania urównoleglania jest [Hunalign](https://github.com/danielvarga/hunalign). Wejściem do programu są dwa pliki, zawierające po jednym segmencie w linii. Wyjściem - plik urównoleglony w wewnętrznym formacie hunaligna.

### Ćwiczenie 3: Odnajdź dowolną stronę, która jest dostępna w wielu językach. Pobierz z tej strony tekst oryginalny (tylko ze strony głównej) oraz przetłumaczony na dowolny inny język. Przy użyciu Pythona przygotuj pliki dla Hunaligna i uruchom go.

Wyjściem z Hunaligna jest plik w specjalnym formacie Hunaligna. Problem jednak w tym, że niestety nie można go w prosty sposób zaimportować do jakiegokolwiek narzędzia typu CAT. Potrzebna jest konwersja do któregoś z bardziej popularnych formatów, np. XLIFF.

XLIFF jest formatem do przechowywania pamięci tłumaczeń, który opiera się na XML-u. Przykładowy plik XLIFF wygląda następująco:

### Ćwiczenie 4: Napisz konwerter formatu hunaligna na XLIFF.

In [87]:
#mi osobiście dedykowana aplikacja zwracała jako wynik plik .txt + umożliwiała wybranie formatu który jest możlwiy do otworzenia w CAT
# pracuję na zestawie danych 
# pl -> https://www.europarl.europa.eu/about-parliament/en/democracy-and-human-rights
# en -> https://www.europarl.europa.eu/about-parliament/en/democracy-and-human-rights
# plik wygenerowany: aligned_pl-en.txt
def convert2xliff(hunalign_file_name,new_xliff_file_name):
    text = """<?xml version="1.0" encoding="UTF-8"?>
                    <xliff xmlns="urn:oasis:names:tc:xliff:document:1.2" version="1.2">
                        <file datatype="plaintext" original="self" source-language="pl" target-language="en">
                            <header>
                                <sxmd:metadata xmlns:sxmd="urn:x-sap:mlt:xliff12:metadata:1.0" xmlns="urn:x-sap:mlt:tsmetadata:1.0">
                                    <developer>Krystian Osinski</developer>
                                </sxmd:metadata>
                            </header>
                            <body>"""
    with open(hunalign_file_name, 'r') as file:
        lines = file.readlines()
        for line in lines:
            source, target, pl = line.strip().split('\t')
            text +=          f"""<trans-unit>
                                    <source>{source}</source>
                                    <target>{target}</target>
                             </trans-unit>"""
    text +=             r"""</body>
                      </file>
                </xliff>"""
    
    with open('output_xml_file.xml', 'w') as xml_file:
        xml_file.write(text)
    
    
    return 0

convert2xliff("aligned_pl-en.txt","xliff_pl_en")

0